# **prepare current working directory (cwd)**

In [126]:
%%bash
# remove everything except this notebook
shopt -s extglob
rm -rf !("notebook.ipynb") 
# to test any error in the terminal, use:
# ipython3 -c "%run notebook.ipynb"

In [2]:
# import tools
import sys, os; sys.path.append(os.path.realpath(os.path.join(os.getcwd(), "../../")))
from tools import *
# while updating modules
# import importlib; importlib.reload(visualize_molecules)
# import importlib; importlib.reload(utils)

import ipywidgets
import glob
import ast
from tqdm import tqdm
import pandas as pd

import rdkit
from rdkit import Chem
import meeko
from meeko import MoleculePreparation
from meeko import PDBQTMolecule
from meeko import RDKitMolCreate
from pymol import cmd
from vina import Vina

# Global variables
dirs_dict = {'raw_ligands':'./raw_ligands/', 'prepared_ligands':'./prepared_ligands/', 
             'raw_receptors':'./raw_receptors/', 'prepared_receptors':'./prepared_receptors/', 
             'vina_scoring':'./vina_scoring/', 'vina_docking':'./vina_docking/'}
vina_seed = 1

In [128]:
# create empty directories
directory_scraping.prepare_directory_from_dict(dirs_dict)

In [129]:
# list directory before execution
!tree .

.
├── notebook.ipynb
├── prepared_ligands
├── prepared_receptors
├── raw_ligands
├── raw_receptors
├── vina_docking
└── vina_scoring

6 directories, 1 file


# **build and prepare ligands**

for comments and more info about this section, take a look at notebook in directory 'example_notebooks/example04 - prepare ligands'

In [130]:
%%file {dirs_dict['raw_ligands']}list_ligands.txt
N#N
CN=C=O
O=Cc1ccc(O)c(OC)c1
COc1cc(C=O)ccc1O
CC(=O)NCCC1=CNc2c1cc(OC)cc2
CC(=O)NCCc1c[nH]c2ccc(OC)cc12
CCc(c1)ccc2[n+]1ccc3c2[nH]c4c3cccc4
CCc1c[n+]2ccc3c4ccccc4[nH]c3c2cc1
CN1CCC[C@H]1c2cccnc2
CCC[C@@H](O)CC\C=C\C=C\C#CC#C\C=C\CO
CCC[C@@H](O)CC/C=C/C=C/C#CC#C/C=C/CO
CC1=C(C(=O)C[C@@H]1OC(=O)[C@@H]2[C@H](C2(C)C)/C=C(\C)/C(=O)OC)C/C=C\C=C
O1C=C[C@H]([C@H]1O2)c3c2cc(OC)c4c3OC(=O)C5=C4CCC(=O)5
OC[C@@H](O1)[C@@H](O)[C@H](O)[C@@H](O)[C@H](O)1
OC[C@@H](O1)[C@@H](O)[C@H](O)[C@@H]2[C@@H]1c3c(O)c(OC)c(O)cc3C(=O)O2
CC(=O)OCCC(/C)=C\C[C@H](C(C)=C)CCC=C
CC[C@H](O1)CC[C@@]12CCCO2
CC(C)[C@@]12C[C@@H]1[C@@H](C)C(=O)C2
OCCc1c(C)[n+](cs1)Cc2cnc(C)nc2N

Writing ./raw_ligands/list_ligands.txt


In [131]:
# create dataframe to register the optimal box size for each ligand
ligands_opt_box_size = pd.DataFrame(columns=['ligand_name', 'optimal_box_size', 'euclid_dist_origin', 'ligand_center'])

with open(dirs_dict['raw_ligands']+'list_ligands.txt') as f:
    ligand_smis = f.readlines()

# clear output directory
directory_scraping.mkdir_or_clear(dirs_dict['prepared_ligands'])
    
for idx, ligand_smi in enumerate(tqdm(ligand_smis), start=1):
    ligand_name = 'ligand_' + f'{idx:03}'
    ligand_smi = ligand_smi.strip()
    # print(ligand_name, ligand_smi)
    # load our ligand from SMILES into RDKit
    lig = rdkit.Chem.MolFromSmiles(ligand_smi)
    # add hydrogens (without regard to pH) 
    protonated_lig = rdkit.Chem.AddHs(lig)
    # generate 3D coordinates for the ligand
    rdkit.Chem.AllChem.EmbedMolecule(protonated_lig)
    # convert to a PDBQT string using the MoleculePreparation class from Meeko.
    meeko_prep = meeko.MoleculePreparation()
    meeko_prep.prepare(protonated_lig)
    lig_pdbqt = meeko_prep.write_pdbqt_string()
    # At this point, pdbqt_string can be written to a file for docking with AutoDock-GPU or Vina, or passed directly to Vina within Python using set_ligand_from_string(pdbqt_string)
    out_file_path = dirs_dict['prepared_ligands'] + ligand_name + '.pdbqt'
    with open(out_file_path, "w") as text_file:
        text_file.write(lig_pdbqt)
    # compute optimal box size using https://www.ncbi.nlm.nih.gov/pmc/articles/PMC4468813/
    optimal_box_size = ligand_preparation.get_optimal_box_size_for_ligand(out_file_path)
    # print("optimal_box_size", optimal_box_size)
    # compute ligand center to make sure it is close to the origin
    ligand_center, euclid_dist_origin = ligand_preparation.get_ligand_center(meeko_prep)
    # update dataframe
    ligands_opt_box_size = ligands_opt_box_size.append({'ligand_name':ligand_name, 'optimal_box_size':optimal_box_size, 'ligand_center':ligand_center, 'euclid_dist_origin':euclid_dist_origin}, ignore_index=True)
        
# save dataframe to csv file
ligands_opt_box_size.to_csv(dirs_dict['prepared_ligands']+'ligands_opt_box_size.csv', sep='\t', index=False)
# print dataframe
ligands_opt_box_size

100%|██████████| 19/19 [00:01<00:00, 10.16it/s]


ligand_name optimal_box_size  euclid_dist_origin          ligand_center
0   ligand_001            2.452            0.000000     [0.00, 0.00, 0.00]
1   ligand_002            5.860            0.906954   [0.90, -0.09, -0.11]
2   ligand_003           10.118            0.439804    [-0.13, 0.42, 0.07]
3   ligand_004           10.068            0.490419   [-0.23, 0.41, -0.14]
4   ligand_005           13.922            0.259950    [0.10, -0.23, 0.06]
5   ligand_006           14.859            0.268021   [-0.01, 0.16, -0.22]
6   ligand_007           14.652            0.568246   [-0.55, -0.11, 0.05]
7   ligand_008           14.560            0.587174  [-0.57, -0.08, -0.14]
8   ligand_009           10.365            0.510678   [0.49, -0.07, -0.11]
9   ligand_010           25.183            1.106018    [1.11, 0.04, -0.01]
10  ligand_011           23.877            1.180385     [1.12, 0.31, 0.21]
11  ligand_012           21.721            0.109793    [0.11, 0.02, -0.01]
12  ligand_013           13.973            0.436202    [0.21, -0.33, 0.20]
13  ligand_014            9.782            0.242223   [-0.18, -0.16, 0.05]
14  ligand_015           14.666            0.273922    [-0.07, 0.26, 0.01]
15  ligand_016           15.874            0.249949    [0.24, -0.04, 0.04]
16  ligand_017            9.709            0.222613    [0.22, -0.02, 0.04]
17  ligand_018            9.549            0.433463   [-0.37, -0.22, 0.07]
18  ligand_019           14.759            0.250968   [-0.13, 0.21, -0.04]

# **download and prepare receptors with pockets**

## batch download receptors

for comments and more info about this section, take a look at notebook in directory 'example02 - download raw molecules'

In [132]:
%%file {dirs_dict['raw_receptors']}list_receptors.txt
3P0V, 3GKW, 5GTY, 6JKG, 6JKH, 3IKA, 5Y9T, 7JXQ, 4LQM, 4LRM, 8A27, 8A2A, 8A2B, 8A2D, 1YY8, 5D41, 6DUK, 6WVZ, 7U98, 7U99, 7U9A, 7LGS, 5ZWJ, 4UV7, 5FED

Writing ./raw_receptors/list_receptors.txt


In [133]:
output = receptor_preparation.batch_download_receptors(dirs_dict['raw_receptors']+'list_receptors.txt', dirs_dict['raw_receptors'])
print(output)
%ls {dirs_dict['raw_receptors']} -l

total 4568
-rw-r--r-- 1 jovyan users 149387 May  1 12:02 1YY8.pdb.gz
-rw-r--r-- 1 jovyan users  74784 May  1 12:02 3GKW.pdb.gz
-rw-r--r-- 1 jovyan users 111769 May  1 12:02 3IKA.pdb.gz
-rw-r--r-- 1 jovyan users 285907 May  1 12:02 3P0V.pdb.gz
-rw-r--r-- 1 jovyan users  60220 May  1 12:02 4LQM.pdb.gz
-rw-r--r-- 1 jovyan users 512373 May  1 12:02 4LRM.pdb.gz
-rw-r--r-- 1 jovyan users 179500 May  1 12:03 4UV7.pdb.gz
-rw-r--r-- 1 jovyan users 117701 May  1 12:03 5D41.pdb.gz
-rw-r--r-- 1 jovyan users 109243 May  1 12:03 5FED.pdb.gz
-rw-r--r-- 1 jovyan users 409171 May  1 12:02 5GTY.pdb.gz
-rw-r--r-- 1 jovyan users  58249 May  1 12:02 5Y9T.pdb.gz
-rw-r--r-- 1 jovyan users  50112 May  1 12:03 5ZWJ.pdb.gz
-rw-r--r-- 1 jovyan users 330158 May  1 12:03 6DUK.pdb.gz
-rw-r--r-- 1 jovyan users  74483 May  1 12:02 6JKG.pdb.gz
-rw-r--r-- 1 jovyan users  77164 May  1 12:02 6JKH.pdb.gz
-rw-r--r-- 1 jovyan users 332094 May  1 12:03 6WVZ.pdb.gz
-rw-r--r-- 1 jovyan users 443702 May  1 12:02 7JXQ.pdb.gz
-rw

## clean receptors and convert them to pdbqt

for comments and more info about this section, take a look at notebook in directory 'example03 - prepare receptors'

In [134]:
pdg_gz_files,_= directory_scraping.list_files_in_dir(directory=dirs_dict['raw_receptors'], search_pattern='*.pdb.gz')
# extract/decompress gz files
for pdg_gz_file in tqdm(pdg_gz_files):
    # print(pdg_gz_file)
    !gzip -d $pdg_gz_file
%ls {dirs_dict['raw_receptors']} -l

100%|██████████| 25/25 [00:28<00:00,  1.13s/it]


total 18332
-rw-r--r-- 1 jovyan users  610821 May  1 12:02 1YY8.pdb
-rw-r--r-- 1 jovyan users  321003 May  1 12:02 3GKW.pdb
-rw-r--r-- 1 jovyan users  459837 May  1 12:02 3IKA.pdb
-rw-r--r-- 1 jovyan users 1117557 May  1 12:02 3P0V.pdb
-rw-r--r-- 1 jovyan users  253287 May  1 12:02 4LQM.pdb
-rw-r--r-- 1 jovyan users 1982070 May  1 12:02 4LRM.pdb
-rw-r--r-- 1 jovyan users  747063 May  1 12:03 4UV7.pdb
-rw-r--r-- 1 jovyan users  490455 May  1 12:03 5D41.pdb
-rw-r--r-- 1 jovyan users  426789 May  1 12:03 5FED.pdb
-rw-r--r-- 1 jovyan users 1697598 May  1 12:02 5GTY.pdb
-rw-r--r-- 1 jovyan users  244134 May  1 12:02 5Y9T.pdb
-rw-r--r-- 1 jovyan users  212220 May  1 12:03 5ZWJ.pdb
-rw-r--r-- 1 jovyan users 1378296 May  1 12:03 6DUK.pdb
-rw-r--r-- 1 jovyan users  304965 May  1 12:02 6JKG.pdb
-rw-r--r-- 1 jovyan users  322380 May  1 12:02 6JKH.pdb
-rw-r--r-- 1 jovyan users 1251450 May  1 12:03 6WVZ.pdb
-rw-r--r-- 1 jovyan users 1746846 May  1 12:02 7JXQ.pdb
-rw-r--r-- 1 jovyan users  842481 Ma

In [135]:
receptor_paths, receptor_names = directory_scraping.list_files_in_dir(directory=dirs_dict['raw_receptors'], search_pattern='*.pdb*')

for i,receptor_path in enumerate(tqdm(receptor_paths)):
    # print("\n", "-"*50, "\n\n", receptor_path, "\n")
    receptor_name = receptor_names[i];
    !pdb_wc $receptor_path
    # -------------------------------------------------------------------------------
    # step01: remove extra chains
    step01_out = dirs_dict['prepared_receptors'] + receptor_name + "_step01.pdb"
    !pdb_selchain -A {receptor_path} > {step01_out}
    # -------------------------------------------------------------------------------
    # step02: remove water molecules
    # [-U]  cleanup type:
    #              'nphs': merge charges and remove non-polar hydrogens
    #              'lps': merge charges and remove lone pairs
    #              'waters': remove water residues
    #              'nonstdres': remove chains composed entirely of residues of
    #                       types other than the standard 20 amino acids
    #              'deleteAltB': remove XX@B atoms and rename XX@A atoms->XX
    #              (default is 'nphs_lps_waters_nonstdres') 
    step02_out = dirs_dict['prepared_receptors'] + receptor_name + "_step02.pdbqt"
    !prepare_receptor -r {step01_out} -o {step02_out} -U 'waters'
    # -------------------------------------------------------------------------------
    # [-e]  delete every nonstd residue from any chain
    #               'True': any residue whose name is not in this list:
    #                       ['CYS','ILE','SER','VAL','GLN','LYS','ASN', 
    #                       'PRO','THR','PHE','ALA','HIS','GLY','ASP', 
    #                       'LEU', 'ARG', 'TRP', 'GLU', 'TYR','MET', 
    #                       'HID', 'HSP', 'HIE', 'HIP', 'CYX', 'CSS']
    #               will be deleted from any chain. 
    #               NB: there are no  nucleic acid residue names at all 
    #               in the list and no metals. 
    #              (default is False which means not to do this)
    step03_out = dirs_dict['prepared_receptors'] + receptor_name + "_step03.pdbqt"
    !prepare_receptor -r {step02_out} -o {step03_out} -e
    # -------------------------------------------------------------------------------
    # [-A]  type(s) of repairs to make: 
    #              'bonds_hydrogens': build bonds and add hydrogens 
    #              'bonds': build a single bond from each atom with no bonds to its closest neighbor
    #              'hydrogens': add hydrogens
    #              'checkhydrogens': add hydrogens only if there are none already
    #              'None': do not make any repairs 
    #              (default is 'None')
    step04_out = dirs_dict['prepared_receptors'] + receptor_name + "_step04.pdbqt"
    !prepare_receptor -r {step03_out} -o {step04_out} -A 'hydrogens'
    # -------------------------------------------------------------------------------
    # change name to last step and remove all middle-stage files
    !mv {step04_out} {dirs_dict['prepared_receptors']}{receptor_name}".pdbqt"
    !rm {dirs_dict['prepared_receptors']}*_step*
    # -------------------------------------------------------------------------------
%ls {dirs_dict['prepared_receptors']} -l

  0%|          | 0/25 [00:00<?, ?it/s]

No. models:	1
No. chains:	4	(   4.0/model)
No. residues:	868	( 868.0/model)
No. atoms:	6604	(6604.0/model)
No. HETATM:	354
Multiple Occ.:	False
Res. Inserts:	False
adding gasteiger charges to peptide
adding gasteiger charges to peptide
'Deleting non-standard residues: from 1YY8_step02
adding gasteiger charges to peptide


  4%|▍         | 1/25 [00:12<04:58, 12.45s/it]

No. models:	1
No. chains:	2	(   2.0/model)
No. residues:	397	( 397.0/model)
No. atoms:	3078	(3078.0/model)
No. HETATM:	206
Multiple Occ.:	False
Res. Inserts:	True
Traceback (most recent call last):
  File "/ADFRsuite/CCSBpckgs/AutoDockTools/Utilities24/prepare_receptor4.py", line 204, in <module>
    mol.buildBondsByDistance()
  File "/ADFRsuite/CCSBpckgs/MolKit/protein.py", line 1176, in buildBondsByDistance
    return bonds
UnboundLocalError: local variable 'bonds' referenced before assignment
Traceback (most recent call last):
  File "/ADFRsuite/CCSBpckgs/AutoDockTools/Utilities24/prepare_receptor4.py", line 148, in <module>
    mols = Read(receptor_filename)
  File "/ADFRsuite/CCSBpckgs/MolKit/__init__.py", line 21, in Read
    raise AssertionError , "%s does't exist" %filename
AssertionError: ./prepared_receptors/3GKW_step02.pdbqt does't exist
Traceback (most recent call last):
  File "/ADFRsuite/CCSBpckgs/AutoDockTools/Utilities24/prepare_receptor4.py", line 148, in <module>
    

  8%|▊         | 2/25 [00:21<03:57, 10.33s/it]

...

No. models:	1
No. chains:	1	(   1.0/model)
No. residues:	272	( 272.0/model)
No. atoms:	2212	(2212.0/model)
No. HETATM:	216
Multiple Occ.:	True
Res. Inserts:	False
WARNING! 8A2B_step01 has 32  atoms with alternate locations named ['A', 'B']!

WARNING! using alternate location A
'Deleting non-standard residues:AKY91101_ from 8A2B_step02
adding gasteiger charges to peptide


 96%|█████████▌| 24/25 [05:18<00:13, 13.70s/it]

No. models:	1
No. chains:	1	(   1.0/model)
No. residues:	281	( 281.0/model)
No. atoms:	2318	(2318.0/model)
No. HETATM:	452
Multiple Occ.:	True
Res. Inserts:	False
WARNING! 8A2D_step01 has 84  atoms with alternate locations named ['A', 'B']!

WARNING! using alternate location A
'Deleting non-standard residues:AEDO1101_AMES1102_AKXY1103_ from 8A2D_step02
adding gasteiger charges to peptide


100%|██████████| 25/25 [05:31<00:00, 13.28s/it]


total 4972
-rw-r--r-- 1 jovyan users 161548 May  1 12:03 1YY8.pdbqt
-rw-r--r-- 1 jovyan users 237148 May  1 12:04 3IKA.pdbqt
-rw-r--r-- 1 jovyan users 235708 May  1 12:04 4LQM.pdbqt
-rw-r--r-- 1 jovyan users 232428 May  1 12:04 4LRM.pdbqt
-rw-r--r-- 1 jovyan users 452188 May  1 12:05 4UV7.pdbqt
-rw-r--r-- 1 jovyan users 234188 May  1 12:05 5D41.pdbqt
-rw-r--r-- 1 jovyan users 225628 May  1 12:05 5FED.pdbqt
-rw-r--r-- 1 jovyan users 229228 May  1 12:05 5GTY.pdbqt
-rw-r--r-- 1 jovyan users 231388 May  1 12:06 5Y9T.pdbqt
-rw-r--r-- 1 jovyan users 200108 May  1 12:06 5ZWJ.pdbqt
-rw-r--r-- 1 jovyan users 238988 May  1 12:06 6DUK.pdbqt
-rw-r--r-- 1 jovyan users 165708 May  1 12:06 6JKG.pdbqt
-rw-r--r-- 1 jovyan users 162508 May  1 12:06 6JKH.pdbqt
-rw-r--r-- 1 jovyan users 233548 May  1 12:07 7JXQ.pdbqt
-rw-r--r-- 1 jovyan users 221628 May  1 12:07 7LGS.pdbqt
-rw-r--r-- 1 jovyan users 226908 May  1 12:07 7U98.pdbqt
-rw-r--r-- 1 jovyan users 235948 May  1 12:07 7U99.pdbqt
-rw-r--r-- 1 jovyan 

## find pockets in receptors

for comments and more info about this section, take a look at notebook in directory 'example07 - find pockets in prepared_receptors'

In [136]:
# List prepared_receptors
receptor_paths, receptor_names = directory_scraping.list_files_in_dir(directory=dirs_dict['prepared_receptors'], search_pattern='*.pdb*')

In [137]:
# Execute fpocket for each receptor
for i,receptor_path in enumerate(tqdm(receptor_paths)):
    # print("\n", "-"*50, "\n\n", receptor_path, "\n")
    receptor_name = receptor_names[i]; #print(receptor_name)
    # -------------------------------------------------------------------------------
    # step01: compute pockets for each receptor
    !fpocket -f {receptor_path} -d > 'prepared_receptors/fp_'{receptor_name}'.csv'
    # print("fpocket finished running")
print("\n", "-"*50, "\n")
%ls {dirs_dict['prepared_receptors']} -l

100%|██████████| 22/22 [00:53<00:00,  2.44s/it]


 -------------------------------------------------- 



total 5164
drwxr-xr-x 2 jovyan users   4096 May  1 12:09 1YY8_out/
-rw-r--r-- 1 jovyan users 161548 May  1 12:03 1YY8.pdbqt
drwxr-xr-x 2 jovyan users   4096 May  1 12:09 3IKA_out/
-rw-r--r-- 1 jovyan users 237148 May  1 12:04 3IKA.pdbqt
drwxr-xr-x 2 jovyan users   4096 May  1 12:09 4LQM_out/
-rw-r--r-- 1 jovyan users 235708 May  1 12:04 4LQM.pdbqt
drwxr-xr-x 2 jovyan users   4096 May  1 12:09 4LRM_out/
-rw-r--r-- 1 jovyan users 232428 May  1 12:04 4LRM.pdbqt
drwxr-xr-x 2 jovyan users   4096 May  1 12:09 4UV7_out/
-rw-r--r-- 1 jovyan users 452188 May  1 12:05 4UV7.pdbqt
drwxr-xr-x 2 jovyan users   4096 May  1 12:09 5D41_out/
-rw-r--r-- 1 jovyan users 234188 May  1 12:05 5D41.pdbqt
drwxr-xr-x 2 jovyan users   4096 May  1 12:09 5FED_out/
-rw-r--r-- 1 jovyan users 225628 May  1 12:05 5FED.pdbqt
drwxr-xr-x 2 jovyan users   4096 May  1 12:09 5GTY_out/
-rw-r--r-- 1 jovyan users 229228 May  1 12:05 5GTY.pdbqt
drwxr-xr-x 2 jovyan users   4096 May  1 12:09 5Y9T_out/
-rw-r--r-- 1 jovyan users 231

In [138]:
# Summarize fpocket data into tables
list_pockets_data = []
for i,receptor_path in enumerate(tqdm(receptor_paths)):
    # print("\n", "-"*50, "\n\n", receptor_path, "\n")
    receptor_name = receptor_names[i];
    pocket_paths = sorted(glob.glob(dirs_dict['prepared_receptors'] + receptor_name + '_out/*.pqr'))
    pockets_data = pd.read_csv(dirs_dict['prepared_receptors']+'fp_' + receptor_name + '.csv',sep=' ',index_col=[0])
    for cav_id, pocket_path in enumerate(pocket_paths, start=1):    
        drug_score = pockets_data["drug_score"].loc[cav_id]
        # compute the box center and size out from the pocket
        pocket_num = cav_id
        cmd.load(filename=pocket_path,format='pqr',object=pocket_num)
        center,size = utils.getbox(selection=pocket_num,extending=0,software='vina')
        center = [center['center_x'], center['center_y'], center['center_z']]
        size = [size['size_x'], size['size_y'], size['size_z']]
        size_max = max(size)
        pockets_data.loc[pocket_num,'receptor_name'] = receptor_name
        pockets_data.loc[pocket_num,'center'] = str(center)
        pockets_data.loc[pocket_num,'size'] = str(size)
        pockets_data.loc[pocket_num,'size_max'] = size_max
    # update pockets data list index. add 'drug_id' to the beginning of each number
    pockets_data.index = pockets_data.index.map(str)
    pockets_data.index = receptor_name + '_' + pockets_data.index
    # append it to list of dataframes
    list_pockets_data.append(pockets_data)

# Merge pockets data and sort it by the drugability score
merged_pockets_data = pd.concat(list_pockets_data).sort_values(by=['drug_score'], ascending=False)
# Save merged data to csv file
merged_pockets_data.to_csv(dirs_dict['prepared_receptors']+'merged_pockets_data.csv', sep='\t')
# Re-read file to make sure everything is fine
# merged_pockets_data = pd.read_csv(dirs_dict['prepared_receptors']+'merged_pockets_data.csv',sep='\t')

100%|██████████| 22/22 [00:01<00:00, 14.55it/s]


In [139]:
# Inspect pockets_data to decide on which pockets will be used from here onwards
merged_pockets_data = pd.read_csv(dirs_dict['prepared_receptors']+'merged_pockets_data.csv',sep='\t')
columns_to_keep = ['cav_id', 'drug_score', 'receptor_name', 'center', 'size', 'size_max', 
                   # 'volume', 'hydrophobicity_score', 'volume_score', 'charge_score','polarity_score', 
                  ]
merged_pockets_data = merged_pockets_data[columns_to_keep]
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(merged_pockets_data)

cav_id  drug_score receptor_name  \
0    7JXQ_17      0.9615          7JXQ   
1    8A2A_14      0.9440          8A2A   
2    6DUK_14      0.9431          6DUK   
3    8A27_12      0.9109          8A27   
4     5GTY_3      0.8579          5GTY   
5     5ZWJ_3      0.8518          5ZWJ   
6    7U98_17      0.8437          7U98   
7    8A2D_11      0.8326          8A2D   
8    5D41_15      0.8111          5D41   
9    4UV7_17      0.7748          4UV7   
10    6JKH_4      0.7725          6JKH   
11    8A2B_1      0.7392          8A2B   
12   4LQM_10      0.6349          4LQM   
13    3IKA_6      0.6058          3IKA   
14    4LQM_7      0.5654          4LQM   
15   7U9A_17      0.5382          7U9A   
16    5Y9T_1      0.5121          5Y9T   
17   6JKG_13      0.4612          6JKG   
18   4LRM_17      0.4579          4LRM   
19    6JKH_1      0.4364          6JKH   
20    7U99_1      0.4147          7U99   
21   6JKG_10      0.3474          6JKG   
22    7U99_7      0.3462          7U99   
23    7LGS_2      0.3095          7LGS   
24    5FED_6      0.3050          5FED   
25   6JKG_12      0.2903          6JKG   
26    6JKH_6      0.2514          6JKH   
27    5FED_5      0.1976          5FED   
28    3IKA_1      0.1965          3IKA   
29    7U99_4      0.1418          7U99   
30   5Y9T_18      0.1061          5Y9T   
31    4UV7_6      0.1054          4UV7   
32    7U9A_4      0.1046          7U9A   
33    6JKG_9      0.1011          6JKG   
34   4UV7_22      0.0919          4UV7   
35    7U98_4      0.0857          7U98   
36    7U9A_9      0.0746          7U9A   
37    1YY8_4      0.0724          1YY8   
38    5D41_3      0.0686          5D41   
39   4UV7_32      0.0644          4UV7   
40   7U99_17      0.0522          7U99   
41    4LQM_5      0.0517          4LQM   
42    4LQM_2      0.0508          4LQM   
43    7U9A_7      0.0504          7U9A   
44    5FED_2      0.0504          5FED   
45    5ZWJ_4      0.0468          5ZWJ   
46    5Y9T_2      0.0466          5Y9T   
47    7U99_3      0.0445          7U99   
48   7U9A_19      0.0442          7U9A   
49   6JKH_14      0.0417          6JKH   
50    6DUK_7      0.0412          6DUK   
51    7JXQ_2      0.0404          7JXQ   
52    8A27_3      0.0370          8A27   
53   4UV7_31      0.0370          4UV7   
54    5Y9T_4      0.0326          5Y9T   
55   4LQM_11      0.0324          4LQM   
56    3IKA_5      0.0321          3IKA   
57    7U9A_5      0.0314          7U9A   
58    5D41_6      0.0305          5D41   
59    1YY8_9      0.0279          1YY8   
60   7JXQ_20      0.0274          7JXQ   
61    7U9A_1      0.0253          7U9A   
62    1YY8_2      0.0253          1YY8   
63   5GTY_10      0.0221          5GTY   
64   7U9A_10      0.0221          7U9A   
65    1YY8_1      0.0212          1YY8   
66    5FED_3      0.0202          5FED   
67   4UV7_16      0.0194          4UV7   
68   7U9A_12      0.0191          7U9A   
69   4UV7_27      0.0190          4UV7   
70   4UV7_28      0.0188          4UV7   
71    5ZWJ_6      0.0186          5ZWJ   
72   4UV7_13      0.0173          4UV7   
73    5Y9T_5      0.0154          5Y9T   
74    5Y9T_8      0.0136          5Y9T   
75    4UV7_5      0.0127          4UV7   
76    5FED_1      0.0125          5FED   
77    8A2A_8      0.0115          8A2A   
78    6DUK_3      0.0114          6DUK   
79    5FED_9      0.0106          5FED   
80    4UV7_3      0.0105          4UV7   
81   5Y9T_16      0.0099          5Y9T   
82    8A2B_9      0.0090          8A2B   
83    3IKA_4      0.0089          3IKA   
84    8A2D_6      0.0080          8A2D   
85   6JKH_12      0.0073          6JKH   
86   7LGS_11      0.0072          7LGS   
87   4UV7_34      0.0072          4UV7   
88   4LQM_14      0.0070          4LQM   
89   4LRM_16      0.0069          4LRM   
90   7U98_14      0.0068          7U98   
91    4LRM_2      0.0068          4LRM   
92    7JXQ_9      0.0067          7JXQ   
93    8A27_6      0.0066          8A27   
94    6JKH_5    

# **vina-score all ligands into filtered-pockets**

for comments and more info about this section, take a look at notebooks in directories 'example08 - score all ligand per protein pockets' and 'example05 - locate ligand inside the box'

In [140]:
merged_pockets_data = pd.read_csv(dirs_dict['prepared_receptors']+'merged_pockets_data.csv',sep='\t')
columns_to_keep = ['cav_id', 'drug_score', 'receptor_name', 'center', 'size', 'size_max', 
                   # 'volume', 'hydrophobicity_score', 'volume_score', 'charge_score','polarity_score', 
                  ]
merged_pockets_data = merged_pockets_data[columns_to_keep]

In [141]:
# when creating the box around the pocket, extend it by a few angstroms on each dimension
box_extra_angstroms = 1

# List prepared molecules
receptor_paths, receptor_names = directory_scraping.list_files_in_dir(directory=dirs_dict['prepared_receptors'], search_pattern='*.pdb*')
ligand_paths, ligand_names = directory_scraping.list_files_in_dir(directory=dirs_dict['prepared_ligands'], search_pattern='*.pdb*')

# load ligands_opt_box_size from csv file
ligands_opt_box_size = pd.read_csv(dirs_dict['prepared_ligands']+'ligands_opt_box_size.csv',sep='\t')
ligands_opt_box_size

ligand_name  optimal_box_size  euclid_dist_origin  \
0   ligand_001             2.452            0.000000   
1   ligand_002             5.860            0.906954   
2   ligand_003            10.118            0.439804   
3   ligand_004            10.068            0.490419   
4   ligand_005            13.922            0.259950   
5   ligand_006            14.859            0.268021   
6   ligand_007            14.652            0.568246   
7   ligand_008            14.560            0.587174   
8   ligand_009            10.365            0.510678   
9   ligand_010            25.183            1.106018   
10  ligand_011            23.877            1.180385   
11  ligand_012            21.721            0.109793   
12  ligand_013            13.973            0.436202   
13  ligand_014             9.782            0.242223   
14  ligand_015            14.666            0.273922   
15  ligand_016            15.874            0.249949   
16  ligand_017             9.709            0.222613   
17  ligand_018             9.549            0.433463   
18  ligand_019            14.759            0.250968   

                  ligand_center  
0      ['0.00', '0.00', '0.00']  
1    ['0.90', '-0.09', '-0.11']  
2     ['-0.13', '0.42', '0.07']  
3    ['-0.23', '0.41', '-0.14']  
4     ['0.10', '-0.23', '0.06']  
5    ['-0.01', '0.16', '-0.22']  
6    ['-0.55', '-0.11', '0.05']  
7   ['-0.57', '-0.08', '-0.14']  
8    ['0.49', '-0.07', '-0.11']  
9     ['1.11', '0.04', '-0.01']  
10     ['1.12', '0.31', '0.21']  
11    ['0.11', '0.02', '-0.01']  
12    ['0.21', '-0.33', '0.20']  
13   ['-0.18', '-0.16', '0.05']  
14    ['-0.07', '0.26', '0.01']  
15    ['0.24', '-0.04', '0.04']  
16    ['0.22', '-0.02', '0.04']  
17   ['-0.37', '-0.22', '0.07']  
18   ['-0.13', '0.21', '-0.04']

In [142]:
# IMPORTANT: CHANGE THIS CELL AS YOU PREFER
# filter the pockets according to your needs
drug_score_min = 0.5
max_num_pockets = 20

pockets_data = merged_pockets_data[merged_pockets_data['drug_score'] >= drug_score_min] \
                        .sort_values(by='drug_score', ascending=False) \
                        [0:max_num_pockets]
pockets_data

cav_id  drug_score receptor_name  \
0   7JXQ_17      0.9615          7JXQ   
1   8A2A_14      0.9440          8A2A   
2   6DUK_14      0.9431          6DUK   
3   8A27_12      0.9109          8A27   
4    5GTY_3      0.8579          5GTY   
5    5ZWJ_3      0.8518          5ZWJ   
6   7U98_17      0.8437          7U98   
7   8A2D_11      0.8326          8A2D   
8   5D41_15      0.8111          5D41   
9   4UV7_17      0.7748          4UV7   
10   6JKH_4      0.7725          6JKH   
11   8A2B_1      0.7392          8A2B   
12  4LQM_10      0.6349          4LQM   
13   3IKA_6      0.6058          3IKA   
14   4LQM_7      0.5654          4LQM   
15  7U9A_17      0.5382          7U9A   
16   5Y9T_1      0.5121          5Y9T   

                                               center  \
0   [16.832000255584717, -40.72749900817871, -24.2...   
1   [-8.648499727249146, -4.48550009727478, -20.59...   
2   [15.683000087738037, 79.89999771118164, -63.55...   
3   [-12.836000442504883, -14.669999599456787, -19...   
4   [-44.54250144958496, 14.454000473022461, -35.4...   
5   [-1.6460000276565552, 55.47800064086914, -4.92...   
6   [8.579499959945679, 20.399500846862793, 19.754...   
7   [-8.102499961853027, -12.559500217437744, 16.4...   
8   [-19.244500160217285, 23.225500106811523, 15.1...   
9   [-11.001500129699707, 4.355999976396561, 19.18...   
10  [-9.286999702453613, 14.549000263214111, -36.2...   
11  [0.12549996376037598, -23.511499404907227, 31....   
12  [-74.74650192260742, -24.37150001525879, -25.0...   
13  [-7.528500080108643, 13.613500118255615, 14.26...   
14  [-66.83650207519531, 4.127000093460083, -25.58...   
15  [48.04050064086914, -4.1730000004172325, 31.27...   
16  [2.4734999537467957, 69.55550003051758, -25.67...   

                                                 size  size_max  
0   [7.939999580383301, 3.3969993591308594, 6.6049...  7.940000  
1   [7.186999797821045, 4.457000255584717, 3.06200...  7.187000  
2   [4.23799991607666, 2.0400009155273438, 1.21699...  4.238000  
3   [8.09000015258789, 6.383999824523926, 8.235999...  8.235999  
4   [3.8530006408691406, 4.700000762939453, 4.8279...  4.827999  
5   [1.4300000667572021, 2.417999267578125, 1.3039...  2.417999  
6   [4.789000034332275, 6.586999893188477, 3.88199...  6.587000  
7   [2.8050003051757812, 3.935000419616699, 4.4609...  4.460999  
8   [4.843000411987305, 1.8930015563964844, 1.6160...  4.843000  
9   [3.8309993743896484, 6.84199994802475, 5.56399...  6.842000  
10  [3.357999801635742, 4.274001121520996, 1.77799...  4.274001  
11    [2.6410000324249268, 3.375, 1.7410011291503906]  3.375000  
12  [5.672996520996094, 5.727001190185547, 6.93099...  6.931000  
13  [2.8389997482299805, 4.619000434875488, 2.8159...  4.619000  
14  [9.925003051757812, 5.938000202178955, 8.26199...  9.925003  
15  [6.0110015869140625, 8.153999999165535, 8.3529...  8.352999  
16  [2.910999894142151, 3.0609970092773438, 9.2080...  9.208000

In [143]:
# %%time
# %%capture --no-stdout

# Create new dataframe to save vina scores
vina_scores = pd.DataFrame(columns=['receptor_name', 'pocket_id', 'ligand_name', 'pocket_box_center', 'vina_box_size', 'vina_score_before_min', 'vina_score_after_min', 'output_path'])

# Iterate over receptors
for receptor_idx,receptor_path in enumerate(tqdm(receptor_paths)):
    # print("\n\n"+"-"*50, "RECEPTOR {} out of {}".format(i+1, len(receptor_paths)), receptor_path, sep='\n')
    receptor_name = receptor_names[receptor_idx];
    # Iterate over the pockets available for the current receptor
    for pocket_idx, pocket_row in tqdm(pockets_data[pockets_data['receptor_name'] == receptor_name].sort_values(by='drug_score', ascending=False).iterrows()):
        pocket_cav_id = pocket_row['cav_id']
        # print('Pocket number: ', pocket_id)
        # print('drug_score: ', pocket_row['drug_score'])
        pocket_box_center = ast.literal_eval(pocket_row['center'])
        # print("pocket_box_center:", pocket_box_center)
        pocket_box_size = pocket_row['size_max']
        # Iterate over ligands
        for ligand_idx,ligand_path in enumerate(tqdm(ligand_paths)):
            # print("\n\t"+"-"*50, "\tLIGAND {} out of {}".format(j+1, len(ligand_paths)),"\t" + ligand_path + "\n", sep='\n')
            ligand_name = ligand_names[ligand_idx];
            # Choose a box size for vina taking into consideration the size of the pocket and the size of the ligand
            ligand_box_size = ligands_opt_box_size.loc[ligands_opt_box_size['ligand_name'] == ligand_name].iloc[0]['optimal_box_size']
            # print("pocket_box_size:", pocket_box_size, "ligand_box_size", ligand_box_size)
            # print("pocket_box_size:", type(pocket_box_size), "ligand_box_size", type(ligand_box_size))
            vina_box_size = [max(pocket_box_size, ligand_box_size) + box_extra_angstroms] * 3
            # print("vina_box_size", vina_box_size)
            # Load ligand and move it to the center of the box
            lig_pdbqt_string = ligand_preparation.translate_ligand_from_pdbqt(pdbqt_path=ligand_path, new_center=pocket_box_center, verbose=False)
            # Prepare vina object
            v = Vina(sf_name='vina', seed=vina_seed)  # default values: class vina.vina.Vina(sf_name='vina', cpu=0, seed=0, no_refine=False, verbosity=1)
            v.set_receptor(receptor_path)
            v.set_ligand_from_string(lig_pdbqt_string)
            v.compute_vina_maps(center=pocket_box_center, box_size=vina_box_size)
            # Score the current pose
            energy = v.score()
            vina_score_before_min = energy[0]
            # print('Score before minimization: %.3f (kcal/mol)' % vina_score_before_min)

            # Minimized locally the current pose
            energy_minimized = v.optimize()
            vina_score_after_min = energy_minimized[0]
            # print('Score after minimization : %.3f (kcal/mol)' % vina_score_after_min)
            output_path = dirs_dict['vina_scoring'] + pocket_cav_id + '_' + ligand_name + '_minimized.pdbqt'
            v.write_pose(output_path, overwrite=True)
            
            # Save vina score in dataframe
            vina_scores = vina_scores.append({'receptor_name': receptor_name, 'pocket_id': pocket_cav_id, 'ligand_name': ligand_name, 
                                              'pocket_box_center': pocket_box_center, 'vina_box_size': vina_box_size, 
                                              'vina_score_before_min': vina_score_before_min, 'vina_score_after_min': vina_score_after_min,
                                             'output_path': output_path}, ignore_index=True)
            # -----------------------------
# Save vina_scoring data to csv file
vina_scores = vina_scores.sort_values(by='vina_score_after_min', ascending=True)
vina_scores.to_csv(dirs_dict['vina_scoring']+'vina_scores.csv', sep='\t', index=False)
# print("\n", "-"*50, "\n")
%ls {dirs_dict['vina_scoring']} -l

  0%|          | 0/22 [00:00<?, ?it/s]
0it [00:00, ?it/s]

0it [00:00, ?it/s]

  0%|          | 0/19 [00:00<?, ?it/s]

  5%|▌         | 1/19 [00:00<00:10,  1.80it/s]


mode |   affinity | dist from best mode
     | (kcal/mol) | rmsd l.b.| rmsd u.b.
-----+------------+----------+----------
   1       -5.855          0          0
   2       -5.675      1.649      5.269
   3       -5.644      2.225      3.457
   4       -5.602      1.386      1.494
   5       -5.425      2.873      6.264
Computing Vina grid ... done.
Performing local search ... done.
Computing Vina grid ... 



 11%|█         | 2/19 [00:00<00:08,  2.12it/s]

done.
Performing local search ... done.




 16%|█▌        | 3/19 [00:01<00:08,  1.99it/s]

...



 89%|████████▉ | 17/19 [00:13<00:01,  1.31it/s]

 95%|█████████▍| 18/19 [00:13<00:00,  1.45it/s]

Computing Vina grid ... done.
Performing local search ... done.




100%|██████████| 19/19 [00:14<00:00,  1.29it/s]

1it [00:14, 14.76s/it]
100%|██████████| 22/22 [03:52<00:00, 10.58s/it]

Computing Vina grid ... done.
Performing local search ... done.


total 1352
-rw-r--r-- 1 jovyan users   641 May  1 12:10 3IKA_6_ligand_001_minimized.pdbqt
-rw-r--r-- 1 jovyan users   676 May  1 12:10 3IKA_6_ligand_002_minimized.pdbqt
-rw-r--r-- 1 jovyan users  1348 May  1 12:10 3IKA_6_ligand_003_minimized.pdbqt
-rw-r--r-- 1 jovyan users  1348 May  1 12:10 3IKA_6_ligand_004_minimized.pdbqt
-rw-r--r-- 1 jovyan users  2044 May  1 12:10 3IKA_6_ligand_005_minimized.pdbqt
-rw-r--r-- 1 jovyan users  2044 May  1 12:10 3IKA_6_ligand_006_minimized.pdbqt
-rw-r--r-- 1 jovyan users  1881 May  1 12:10 3IKA_6_ligand_007_minimized.pdbqt
-rw-r--r-- 1 jovyan users  1881 May  1 12:10 3IKA_6_ligand_008_minimized.pdbqt
-rw-r--r-- 1 jovyan users  1251 May  1 12:10 3IKA_6_ligand_009_minimized.pdbqt
-rw-r--r-- 1 jovyan users  2490 May  1 12:10 3IKA_6_ligand_010_minimized.pdbqt
-rw-r--r-- 1 jovyan users  2490 May  1 12:10 3IKA_6_ligand_011_minimized.pdbqt
-rw-r--r-- 1 jovyan users  3207 May  1 12:10 3IKA_6_ligand_012_minimized.pdbqt
-rw-r--r-- 1 jovyan users  2406 May  1 12

In [144]:
# load data from file
vina_scores = pd.read_csv(dirs_dict['vina_scoring']+'vina_scores.csv',sep='\t')
# Inspect vina_scoring data to decide on which dockings will be used from here onwards
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(vina_scores)

receptor_name pocket_id ligand_name  \
0            8A2D   8A2D_11  ligand_014   
1            8A2D   8A2D_11  ligand_018   
2            8A2D   8A2D_11  ligand_015   
3            8A2D   8A2D_11  ligand_017   
4            4LQM    4LQM_7  ligand_014   
5            7U9A   7U9A_17  ligand_011   
6            8A2D   8A2D_11  ligand_007   
7            8A2A   8A2A_14  ligand_013   
8            7JXQ   7JXQ_17  ligand_007   
9            7U9A   7U9A_17  ligand_009   
10           8A2A   8A2A_14  ligand_019   
11           7JXQ   7JXQ_17  ligand_008   
12           8A2D   8A2D_11  ligand_003   
13           4LQM    4LQM_7  ligand_018   
14           7U9A   7U9A_17  ligand_010   
15           8A27   8A27_12  ligand_006   
16           7JXQ   7JXQ_17  ligand_009   
17           7U98   7U98_17  ligand_013   
18           3IKA    3IKA_6  ligand_015   
19           8A2A   8A2A_14  ligand_005   
20           4LQM    4LQM_7  ligand_007   
21           7U98   7U98_17  ligand_014   
22           7U9A   7U9A_17  ligand_014   
23           7U9A   7U9A_17  ligand_006   
24           5GTY    5GTY_3  ligand_018   
25           4LQM    4LQM_7  ligand_012   
26           5GTY    5GTY_3  ligand_003   
27           7U9A   7U9A_17  ligand_012   
28           8A2A   8A2A_14  ligand_014   
29           3IKA    3IKA_6  ligand_006   
30           4LQM   4LQM_10  ligand_014   
31           7U98   7U98_17  ligand_009   
32           4LQM   4LQM_10  ligand_015   
33           8A2A   8A2A_14  ligand_006   
34           8A2A   8A2A_14  ligand_003   
35           7U9A   7U9A_17  ligand_017   
36           6DUK   6DUK_14  ligand_015   
37           8A2A   8A2A_14  ligand_018   
38           7JXQ   7JXQ_17  ligand_019   
39           6JKH    6JKH_4  ligand_014   
40           6DUK   6DUK_14  ligand_005   
41           4UV7   4UV7_17  ligand_008   
42           5GTY    5GTY_3  ligand_008   
43           5D41   5D41_15  ligand_005   
44           6JKH    6JKH_4  ligand_019   
45           4LQM    4LQM_7  ligand_006   
46           8A2A   8A2A_14  ligand_004   
47           4LQM    4LQM_7  ligand_009   
48           7JXQ   7JXQ_17  ligand_015   
49           8A27   8A27_12  ligand_005   
50           7JXQ   7JXQ_17  ligand_018   
51           3IKA    3IKA_6  ligand_008   
52           4LQM   4LQM_10  ligand_003   
53           8A2A   8A2A_14  ligand_009   
54           5ZWJ    5ZWJ_3  ligand_017   
55           5ZWJ    5ZWJ_3  ligand_008   
56           5ZWJ    5ZWJ_3  ligand_018   
57           4UV7   4UV7_17  ligand_017   
58           7JXQ   7JXQ_17  ligand_017   
59           4LQM   4LQM_10  ligand_009   
60           3IKA    3IKA_6  ligand_017   
61           4LQM    4LQM_7  ligand_015   
62           7U98   7U98_17  ligand_017   
63           7JXQ   7JXQ_17  ligand_014   
64           7JXQ   7JXQ_17  ligand_013   
65           5D41   5D41_15  ligand_004   
66           7U9A   7U9A_17  ligand_018   
67           8A2D   8A2D_11  ligand_011   
68           5Y9T    5Y9T_1  ligand_015   
69           8A2B    8A2B_1  ligand_015   
70           7JXQ   7JXQ_17  ligand_010   
71           6DUK   6DUK_14  ligand_014   
72           3IKA    3IKA_6  ligand_014   
73           8A2A   8A2A_14  ligand_017   
74           5ZWJ    5ZWJ_3  ligand_012   
75           3IKA    3IKA_6  ligand_005   
76           7JXQ   7JXQ_17  ligand_005   
77           6JKH    6JKH_4  ligand_016   
78           8A27   8A27_12  ligand_004   
79           4UV7   4UV7_17  ligand_018   
80           3IKA    3IKA_6  ligand_018   
81           5Y9T    5Y9T_1  ligand_007   
82           5D41   5D41_15  ligand_012   
83           5GTY    5GTY_3  ligand_015   
84           8A27   8A27_12  ligand_014   
85           4LQM   4LQM_10  ligand_004   
86           4LQM    4LQM_7  ligand_017   
87           5D41   5D41_15  ligand_014   
88           4LQM    4LQM_7  ligand_013   
89           5GTY    5GTY_3  ligand_006   
90           5GTY    5GTY_3  ligand_011   
91           5Y9T    5Y9T_1  ligand_014   
92   

# **vina-dock filtered-ligands into filtered-pockets**

for comments and more info about this section, take a look at notebook in directory 'example09 - multiple docking'

In [145]:
# IMPORTANT: CHANGE THIS CELL AS YOU PREFER
# filter the vina_scores according to your needs
vina_score_max = -1
max_num_dockings = 20

vina_scores = pd.read_csv(dirs_dict['vina_scoring']+'vina_scores.csv',sep='\t')
vina_scores_filtered = vina_scores[vina_scores['vina_score_after_min'] <= vina_score_max] \
                        .sort_values(by='vina_score_after_min', ascending=True) \
                        [0:max_num_dockings]
vina_scores_filtered

receptor_name pocket_id ligand_name  \
0           8A2D   8A2D_11  ligand_014   
1           8A2D   8A2D_11  ligand_018   
2           8A2D   8A2D_11  ligand_015   
3           8A2D   8A2D_11  ligand_017   
4           4LQM    4LQM_7  ligand_014   
5           7U9A   7U9A_17  ligand_011   
6           8A2D   8A2D_11  ligand_007   
7           8A2A   8A2A_14  ligand_013   
8           7JXQ   7JXQ_17  ligand_007   
9           7U9A   7U9A_17  ligand_009   
10          8A2A   8A2A_14  ligand_019   
11          7JXQ   7JXQ_17  ligand_008   
12          8A2D   8A2D_11  ligand_003   
13          4LQM    4LQM_7  ligand_018   
14          7U9A   7U9A_17  ligand_010   
15          8A27   8A27_12  ligand_006   
16          7JXQ   7JXQ_17  ligand_009   
17          7U98   7U98_17  ligand_013   
18          3IKA    3IKA_6  ligand_015   
19          8A2A   8A2A_14  ligand_005   

                                    pocket_box_center  \
0   [-8.102499961853027, -12.559500217437744, 16.4...   
1   [-8.102499961853027, -12.559500217437744, 16.4...   
2   [-8.102499961853027, -12.559500217437744, 16.4...   
3   [-8.102499961853027, -12.559500217437744, 16.4...   
4   [-66.83650207519531, 4.127000093460083, -25.58...   
5   [48.04050064086914, -4.1730000004172325, 31.27...   
6   [-8.102499961853027, -12.559500217437744, 16.4...   
7   [-8.648499727249146, -4.48550009727478, -20.59...   
8   [16.832000255584717, -40.72749900817871, -24.2...   
9   [48.04050064086914, -4.1730000004172325, 31.27...   
10  [-8.648499727249146, -4.48550009727478, -20.59...   
11  [16.832000255584717, -40.72749900817871, -24.2...   
12  [-8.102499961853027, -12.559500217437744, 16.4...   
13  [-66.83650207519531, 4.127000093460083, -25.58...   
14  [48.04050064086914, -4.1730000004172325, 31.27...   
15  [-12.836000442504883, -14.669999599456787, -19...   
16  [16.832000255584717, -40.72749900817871, -24.2...   
17  [8.579499959945679, 20.399500846862793, 19.754...   
18  [-7.528500080108643, 13.613500118255615, 14.26...   
19  [-8.648499727249146, -4.48550009727478, -20.59...   

                                        vina_box_size  vina_score_before_min  \
0                            [10.782, 10.782, 10.782]                 11.240   
1                            [10.549, 10.549, 10.549]                 15.292   
2                            [15.666, 15.666, 15.666]                 76.179   
3                            [10.709, 10.709, 10.709]                 16.697   
4   [10.925003051757812, 10.925003051757812, 10.92...                 34.054   
5                            [24.877, 24.877, 24.877]                 61.316   
6                            [15.652, 15.652, 15.652]                 80.134   
7                            [14.973, 14.973, 14.973]                 16.316   
8                            [15.652, 15.652, 15.652]                 10.849   
9                            [11.365, 11.365, 11.365]                 35.258   
10                           [15.759, 15.759, 15.759]                 12.658   
11                              [15.56, 15.56, 15.56]                  8.303   
12                           [11.118, 11.118, 11.118]                 15.139   
13  [10.925003051757812, 10.925003051757812, 10.92...                 42.234   
14                           [26.183, 26.183, 26.183]                 87.218   
15                           [15.859, 15.859, 15.859]                 53.593   
16                           [11.365, 11.365, 11.365]                  0.060   
17                           [14.973, 14.973, 14.973]                 63.041   
18                           [15.666, 15.666, 15.666]                 25.122   
19                           [14.922, 14.922, 14.922]                 14.928   

    vina_score_after_min                                        output_path  
0                 -5.613  ./vina_scoring/8A2D_11_ligand_014_minimized.pdbqt  
1                 -5.011  ./vina_scoring/8A2D_11_ligand_018_minimized.pdbqt  
2      

<span style='background:lightblue'> **Important** </span>

<span style='background:lightblue'>
from the official website: https://autodock-vina.readthedocs.io/en/latest/docking_python.html
</span>

```python
# Dock the ligand
v.dock(exhaustiveness=32, n_poses=20)
v.write_poses('1iep_ligand_vina_out.pdbqt', n_poses=5, overwrite=True)
```

<span style='background:lightblue'>
Finally, we run the molecular docking. Here we will ask Vina to run 32 consecutive Monte-Carlo samplings using the `exhaustiveness` argument and store 20 poses (n_poses) during the search. At the end, we will write a PDBQT file called `1iep_ligand_vina_out.pdbqt` containing only the 5 first poses (`n_poses`), ranked by score. Of course, this can be change to 20 to include all the poses that were saved during the calculations, at the condition that the energy difference between the best pose and the 20th pose if less than 3 kcal/mol. This behavior can be changed using the `energy_range` argument to an higher value.
</span>

In [146]:
vina_exhaustiveness=32    # default:32 
vina_n_poses_to_dock=20   # default:20
vina_n_poses_to_write=5  # default:5

In [147]:
# Create new dataframe to save vina scores
vina_dockings = pd.DataFrame(columns=['receptor_name', 'pocket_id', 'ligand_name', 'vina_docking_best', 'vina_docking_values', 'pocket_box_center', 'vina_box_size', 'output_path'])

for scoring_row_idx, scoring_row in tqdm(vina_scores_filtered.iterrows()):
# for scoring_row_idx, scoring_row in tqdm(vina_scores_filtered.iterrows()):
    print("-"*200)
    # print("scoring_row", scoring_row)
    receptor_name = scoring_row['receptor_name']
    receptor_path = dirs_dict['prepared_receptors'] + receptor_name + '.pdbqt'
    pocket_id = scoring_row['pocket_id']
    pocket_box_center = ast.literal_eval(scoring_row['pocket_box_center'])
    vina_box_size = ast.literal_eval(scoring_row['vina_box_size'])
    ligand_name = scoring_row['ligand_name']
    ligand_path = dirs_dict['prepared_ligands'] + ligand_name + '.pdbqt'
    lig_pdbqt_string = ligand_preparation.translate_ligand_from_pdbqt(pdbqt_path=ligand_path, new_center=pocket_box_center, verbose=False)
    # print("scoring_row_idx", scoring_row_idx, "pocket_id", pocket_id, "ligand_name", ligand_name)
    display(vina_scores_filtered.iloc[[scoring_row_idx]])
    
    # Prepare vina object
    v = Vina(sf_name='vina', seed=vina_seed)  # default values: class vina.vina.Vina(sf_name='vina', cpu=0, seed=0, no_refine=False, verbosity=1)
    v.set_receptor(receptor_path)
    v.set_ligand_from_string(lig_pdbqt_string)
    v.compute_vina_maps(center=pocket_box_center, box_size=vina_box_size)
    
    # Score the current pose
    energy = v.score()
    vina_score_before_min = energy[0]
    print('Score before minimization: %.3f (kcal/mol)' % vina_score_before_min)

    # Minimized locally the current pose
    energy_minimized = v.optimize()
    vina_score_after_min = energy_minimized[0]
    print('Score after minimization : %.3f (kcal/mol)' % vina_score_after_min)
    # v.write_pose(dirs_dict['vina_scoring'] + pocket_cav_id + '_' + ligand_name + '_minimized.pdbqt', overwrite=True)
    
    # Dock the ligand
    v.dock(exhaustiveness=vina_exhaustiveness, n_poses=vina_n_poses_to_dock)
    output_path = dirs_dict['vina_docking'] + pocket_id + '_' + ligand_name + '_vina_out.pdbqt'
    v.write_poses(output_path, n_poses=vina_n_poses_to_write, overwrite=True)
    print("docking finished")
    
    # Get docking values from output
    vina_docking_values = utils.get_scores_from_pdbqt(output_path)
    
    # Save vina score in dataframe
    vina_dockings = vina_dockings.append({'receptor_name': receptor_name, 'pocket_id': pocket_id, 'ligand_name': ligand_name, 
                                          'vina_docking_best': min(vina_docking_values), 'vina_docking_values': vina_docking_values,
                                          'pocket_box_center': pocket_box_center, 'vina_box_size': vina_box_size,
                                          'output_path': output_path}, ignore_index=True)

# Save vina_scoring data to csv file
vina_dockings = vina_dockings.sort_values(by='vina_docking_best', ascending=True)
vina_dockings.to_csv(dirs_dict['vina_docking']+'vina_dockings.csv', sep='\t', index=False)
%ls {dirs_dict['vina_docking']} -l    

0it [00:00, ?it/s]

--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------


receptor_name pocket_id ligand_name  \
0          8A2D   8A2D_11  ligand_014   

                                   pocket_box_center  \
0  [-8.102499961853027, -12.559500217437744, 16.4...   

              vina_box_size  vina_score_before_min  vina_score_after_min  \
0  [10.782, 10.782, 10.782]                  11.24                -5.613   

                                         output_path  
0  ./vina_scoring/8A2D_11_ligand_014_minimized.pdbqt

Computing Vina grid ... done.
Score before minimization: 14.844 (kcal/mol)
Score after minimization : -5.403 (kcal/mol)


1it [00:34, 34.31s/it]

...

docking finished
--------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------


receptor_name pocket_id ligand_name  \
19          8A2A   8A2A_14  ligand_005   

                                    pocket_box_center  \
19  [-8.648499727249146, -4.48550009727478, -20.59...   

               vina_box_size  vina_score_before_min  vina_score_after_min  \
19  [14.922, 14.922, 14.922]                 14.928                -3.377   

                                          output_path  
19  ./vina_scoring/8A2A_14_ligand_005_minimized.pdbqt

20it [17:42, 53.15s/it]


mode |   affinity | dist from best mode
     | (kcal/mol) | rmsd l.b.| rmsd u.b.
-----+------------+----------+----------
   1       -5.147          0          0
   2        -5.03      2.027      5.932
   3       -4.856      2.279      4.075
   4       -4.855      2.752      4.756
   5       -4.844      2.151      5.259
   6       -4.804      1.611      6.187
   7       -4.676      1.893       5.56
   8       -4.617      1.507      5.454
   9       -4.596       1.84      3.918
  10       -4.575      2.488      5.345
  11       -4.565      2.243      6.119
  12       -4.532      2.099       4.91
  13       -4.489      2.392      3.367
  14        -4.44      2.252      5.803
  15         -4.4      3.297      6.056
  16       -4.333      1.697      5.892
  17       -4.313      2.791      5.474
  18       -4.268      1.783      6.189
  19       -4.261      2.859      6.799
Computing Vina grid ... Score before minimization: 18.192 (kcal/mol)
Score after minimization : -2.046 (kcal/mol)
don

total 252
-rw-r--r-- 1 jovyan users 15580 May  1 12:30 3IKA_6_ligand_015_vina_out.pdbqt
-rw-r--r-- 1 jovyan users  9900 May  1 12:17 4LQM_7_ligand_014_vina_out.pdbqt
-rw-r--r-- 1 jovyan users  7105 May  1 12:24 4LQM_7_ligand_018_vina_out.pdbqt
-rw-r--r-- 1 jovyan users 10500 May  1 12:21 7JXQ_17_ligand_007_vina_out.pdbqt
-rw-r--r-- 1 jovyan users 10500 May  1 12:23 7JXQ_17_ligand_008_vina_out.pdbqt
-rw-r--r-- 1 jovyan users  7350 May  1 12:28 7JXQ_17_ligand_009_vina_out.pdbqt
-rw-r--r-- 1 jovyan users 13125 May  1 12:29 7U98_17_ligand_013_vina_out.pdbqt
-rw-r--r-- 1 jovyan users  7350 May  1 12:22 7U9A_17_ligand_009_vina_out.pdbqt
-rw-r--r-- 1 jovyan users 13545 May  1 12:27 7U9A_17_ligand_010_vina_out.pdbqt
-rw-r--r-- 1 jovyan users 13545 May  1 12:20 7U9A_17_ligand_011_vina_out.pdbqt
-rw-r--r-- 1 jovyan users 11315 May  1 12:28 8A27_12_ligand_006_vina_out.pdbqt
-rw-r--r-- 1 jovyan users 11315 May  1 12:31 8A2A_14_ligand_005_vina_out.pdbqt
-rw-r--r-- 1 jovyan users 13125 May  1 12:21 

In [148]:
vina_dockings

receptor_name pocket_id ligand_name  vina_docking_best  \
6           8A2D   8A2D_11  ligand_007             -8.259   
2           8A2D   8A2D_11  ligand_015             -7.289   
7           8A2A   8A2A_14  ligand_013             -6.315   
9           7U9A   7U9A_17  ligand_009             -5.947   
0           8A2D   8A2D_11  ligand_014             -5.737   
11          7JXQ   7JXQ_17  ligand_008             -5.729   
8           7JXQ   7JXQ_17  ligand_007             -5.683   
17          7U98   7U98_17  ligand_013             -5.549   
1           8A2D   8A2D_11  ligand_018             -5.541   
15          8A27   8A27_12  ligand_006             -5.472   
12          8A2D   8A2D_11  ligand_003             -5.327   
3           8A2D   8A2D_11  ligand_017             -5.310   
14          7U9A   7U9A_17  ligand_010             -5.284   
19          8A2A   8A2A_14  ligand_005             -5.154   
18          3IKA    3IKA_6  ligand_015             -5.147   
4           4LQM    4LQM_7  ligand_014             -5.140   
5           7U9A   7U9A_17  ligand_011             -4.869   
10          8A2A   8A2A_14  ligand_019             -4.680   
16          7JXQ   7JXQ_17  ligand_009             -4.584   
13          4LQM    4LQM_7  ligand_018             -4.159   

                         vina_docking_values  \
6    [-8.259, -8.253, -7.794, -7.787, -7.75]   
2    [-7.289, -7.03, -6.902, -6.842, -6.689]   
7    [-6.315, -6.274, -5.782, -5.777, -5.77]   
9        [-5.947, -5.7, -5.48, -5.1, -5.083]   
0    [-5.737, -5.71, -5.667, -5.556, -5.358]   
11  [-5.729, -5.634, -5.589, -5.482, -5.342]   
8    [-5.683, -5.414, -5.34, -5.297, -5.236]   
17      [-5.549, -5.4, -5.322, -5.228, -5.2]   
1   [-5.541, -5.249, -5.159, -5.146, -5.028]   
15  [-5.472, -5.052, -4.951, -4.801, -4.762]   
12  [-5.327, -4.952, -4.883, -4.856, -4.814]   
3    [-5.31, -5.308, -5.278, -5.187, -5.093]   
14  [-5.284, -5.184, -5.104, -4.996, -4.974]   
19  [-5.154, -4.856, -4.846, -4.784, -4.766]   
18   [-5.147, -5.03, -4.856, -4.855, -4.844]   
4    [-5.14, -5.108, -5.031, -4.867, -4.746]   
5    [-4.869, -4.866, -4.846, -4.81, -4.788]   
10   [-4.68, -4.661, -4.456, -4.414, -4.388]   
16  [-4.584, -4.291, -4.161, -4.139, -3.934]   
13   [-4.159, -3.957, -3.92, -3.872, -3.754]   

                                    pocket_box_center  \
6   [-8.102499961853027, -12.559500217437744, 16.4...   
2   [-8.102499961853027, -12.559500217437744, 16.4...   
7   [-8.648499727249146, -4.48550009727478, -20.59...   
9   [48.04050064086914, -4.1730000004172325, 31.27...   
0   [-8.102499961853027, -12.559500217437744, 16.4...   
11  [16.832000255584717, -40.72749900817871, -24.2...   
8   [16.832000255584717, -40.72749900817871, -24.2...   
17  [8.579499959945679, 20.399500846862793, 19.754...   
1   [-8.102499961853027, -12.559500217437744, 16.4...   
15  [-12.836000442504883, -14.669999599456787, -19...   
12  [-8.102499961853027, -12.559500217437744, 16.4...   
3   [-8.102499961853027, -12.559500217437744, 16.4...   
14  [48.04050064086914, -4.1730000004172325, 31.27...   
19  [-8.648499727249146, -4.48550009727478, -20.59...   
18  [-7.528500080108643, 13.613500118255615, 14.26...   
4   [-66.83650207519531, 4.127000093460083, -25.58...   
5   [48.04050064086914, -4.1730000004172325, 31.27...   
10  [-8.648499727249146, -4.48550009727478, -20.59...   
16  [16.832000255584717, -40.72749900817871, -24.2...   
13  [-66.83650207519531, 4.127000093460083, -25.58...   

                                        vina_box_size  \
6                            [15.652, 15.652, 15.652]   
2                            [15.666, 15.666, 15.666]   
7                            [14.973, 14.973, 14.973]   
9                            [11.365, 11.365, 11.365]   
0                            [10.782, 10.782, 10.782]   
11                              [15.56, 15.56, 15.56]   
8                            [15.652, 15.652, 15.652]   
17                           [14.973, 14.973, 14.973]   
1

## list directory after execution

In [149]:
!tree .

.
├── notebook.ipynb
├── prepared_ligands
│   ├── ligand_001.pdbqt
│   ├── ligand_002.pdbqt
│   ├── ligand_003.pdbqt
│   ├── ligand_004.pdbqt
│   ├── ligand_005.pdbqt
│   ├── ligand_006.pdbqt
│   ├── ligand_007.pdbqt
│   ├── ligand_008.pdbqt
│   ├── ligand_009.pdbqt
│   ├── ligand_010.pdbqt
│   ├── ligand_011.pdbqt
│   ├── ligand_012.pdbqt
│   ├── ligand_013.pdbqt
│   ├── ligand_014.pdbqt
│   ├── ligand_015.pdbqt
│   ├── ligand_016.pdbqt
│   ├── ligand_017.pdbqt
│   ├── ligand_018.pdbqt
│   ├── ligand_019.pdbqt
│   └── ligands_opt_box_size.csv
├── prepared_receptors
│   ├── 1YY8_out
│   │   ├── pocket10_atm.pdb
│   │   ├── pocket10_env_atm.pdb
│   │   ├── pocket10_vert.pqr
│   │   ├── pocket11_atm.pdb
│   │   ├── pocket11_env_atm.pdb
│   │   ├── pocket11_vert.pqr
│   │   ├── pocket1_atm.pdb
│   │   ├── pocket1_env_atm.pdb
│   │   ├── pocket1_vert.pqr
│   │   ├── pocket2_atm.pdb
│   │   ├── pocket2_env_atm.pdb
│   │   ├── pocket2_vert.pqr
│   │   ├── pocket3_atm.pdb
│   │   ├── pocket3_

# **visualize**

for comments and more info about this section, take a look at notebook in directory 'example06 - visualize molecules'

## visualize ligands

ref: https://birdlet.github.io/2019/10/02/py3dmol_example/

In [5]:
# List prepared molecules
# receptor_paths, receptor_names = directory_scraping.list_files_in_dir(directory=dirs_dict['prepared_receptors'], search_pattern='*.pdb*')
ligand_paths, ligand_names = directory_scraping.list_files_in_dir(directory=dirs_dict['prepared_ligands'], search_pattern='*.pdb*')
mols = [parse_molecules.MolFromPDBQTBlock(block=open(ligand_path,'r').read(),sanitize=False,removeHs=False) 
        for ligand_path in ligand_paths]

In [6]:
def ligand_selector(idx, style, show_surface):
    mol = mols[idx-1]
    return visualize_molecules.show_3d_ligand(mol, style=style, surface=show_surface).show()

# Interactive widgets
ipywidgets.interact(ligand_selector, 
         idx = ipywidgets.IntSlider(min=1,max=len(mols), step=1),
         style = ipywidgets.Dropdown(options=['line', 'stick', 'sphere'], value='stick', description='Style:'),
         show_surface = ipywidgets.Checkbox(value=False, description='show surface')
        )

interactive(children=(IntSlider(value=1, description='idx', max=19, min=1), Dropdown(description='Style:', ind…

<function __main__.ligand_selector(idx, style, show_surface)>

## visualize receptors with pockets

In [7]:
# List prepared molecules
receptor_paths, receptor_names = directory_scraping.list_files_in_dir(directory=dirs_dict['prepared_receptors'], search_pattern='*.pdb*')

In [8]:
def receptor_selector(idx, show_pockets, show_drug_score, show_surface):
    receptor_path, receptor_name = receptor_paths[idx-1], receptor_names[idx-1]
    pocket_paths = sorted(glob.glob(dirs_dict['prepared_receptors'] + receptor_name + '_out/*.pqr'))
    pockets_data = pd.read_csv(dirs_dict['prepared_receptors'] + 'fp_' + receptor_name + '.csv',sep=' ',index_col=[0])
    visualize_molecules.show_3d_receptor(receptor_path, receptor_name, 
                            show_pockets=show_pockets, show_drug_score=show_drug_score, show_surface=show_surface, 
                            pocket_paths=pocket_paths, pockets_data=pockets_data).show()
    print("receptor_name:", receptor_name)

# Interactive widgets
ipywidgets.interact(receptor_selector, 
                    idx = ipywidgets.IntSlider(min=1,max=len(receptor_paths), step=1),
                    # style = ipywidgets.Dropdown(options=['line', 'stick', 'sphere'], value='stick', description='Style:'),
                    show_pockets = ipywidgets.Checkbox(value=True, description='show pockets'),
                    show_drug_score = ipywidgets.Checkbox(value=False, description='show pockets drug_score'),
                    show_surface = ipywidgets.Checkbox(value=False, description='show surface')
        )

interactive(children=(IntSlider(value=1, description='idx', max=22, min=1), Checkbox(value=True, description='…

<function __main__.receptor_selector(idx, show_pockets, show_drug_score, show_surface)>

## visualize scorings

In [9]:
# IMPORTANT: CHANGE THIS CELL AS YOU PREFER
# filter the vina_scores according to your needs
vina_score_max = -1
max_num_dockings = 20

vina_scores = pd.read_csv(dirs_dict['vina_scoring']+'vina_scores.csv',sep='\t')
vina_scores_filtered = vina_scores[vina_scores['vina_score_after_min'] <= vina_score_max] \
                        .sort_values(by='vina_score_after_min', ascending=True) \
                        [0:max_num_dockings]
vina_scores_filtered

receptor_name pocket_id ligand_name  \
0           8A2D   8A2D_11  ligand_014   
1           8A2D   8A2D_11  ligand_018   
2           8A2D   8A2D_11  ligand_015   
3           8A2D   8A2D_11  ligand_017   
4           4LQM    4LQM_7  ligand_014   
5           7U9A   7U9A_17  ligand_011   
6           8A2D   8A2D_11  ligand_007   
7           8A2A   8A2A_14  ligand_013   
8           7JXQ   7JXQ_17  ligand_007   
9           7U9A   7U9A_17  ligand_009   
10          8A2A   8A2A_14  ligand_019   
11          7JXQ   7JXQ_17  ligand_008   
12          8A2D   8A2D_11  ligand_003   
13          4LQM    4LQM_7  ligand_018   
14          7U9A   7U9A_17  ligand_010   
15          8A27   8A27_12  ligand_006   
16          7JXQ   7JXQ_17  ligand_009   
17          7U98   7U98_17  ligand_013   
18          3IKA    3IKA_6  ligand_015   
19          8A2A   8A2A_14  ligand_005   

                                    pocket_box_center  \
0   [-8.102499961853027, -12.559500217437744, 16.4...   
1   [-8.102499961853027, -12.559500217437744, 16.4...   
2   [-8.102499961853027, -12.559500217437744, 16.4...   
3   [-8.102499961853027, -12.559500217437744, 16.4...   
4   [-66.83650207519531, 4.127000093460083, -25.58...   
5   [48.04050064086914, -4.1730000004172325, 31.27...   
6   [-8.102499961853027, -12.559500217437744, 16.4...   
7   [-8.648499727249146, -4.48550009727478, -20.59...   
8   [16.832000255584717, -40.72749900817871, -24.2...   
9   [48.04050064086914, -4.1730000004172325, 31.27...   
10  [-8.648499727249146, -4.48550009727478, -20.59...   
11  [16.832000255584717, -40.72749900817871, -24.2...   
12  [-8.102499961853027, -12.559500217437744, 16.4...   
13  [-66.83650207519531, 4.127000093460083, -25.58...   
14  [48.04050064086914, -4.1730000004172325, 31.27...   
15  [-12.836000442504883, -14.669999599456787, -19...   
16  [16.832000255584717, -40.72749900817871, -24.2...   
17  [8.579499959945679, 20.399500846862793, 19.754...   
18  [-7.528500080108643, 13.613500118255615, 14.26...   
19  [-8.648499727249146, -4.48550009727478, -20.59...   

                                        vina_box_size  vina_score_before_min  \
0                            [10.782, 10.782, 10.782]                 11.240   
1                            [10.549, 10.549, 10.549]                 15.292   
2                            [15.666, 15.666, 15.666]                 76.179   
3                            [10.709, 10.709, 10.709]                 16.697   
4   [10.925003051757812, 10.925003051757812, 10.92...                 34.054   
5                            [24.877, 24.877, 24.877]                 61.316   
6                            [15.652, 15.652, 15.652]                 80.134   
7                            [14.973, 14.973, 14.973]                 16.316   
8                            [15.652, 15.652, 15.652]                 10.849   
9                            [11.365, 11.365, 11.365]                 35.258   
10                           [15.759, 15.759, 15.759]                 12.658   
11                              [15.56, 15.56, 15.56]                  8.303   
12                           [11.118, 11.118, 11.118]                 15.139   
13  [10.925003051757812, 10.925003051757812, 10.92...                 42.234   
14                           [26.183, 26.183, 26.183]                 87.218   
15                           [15.859, 15.859, 15.859]                 53.593   
16                           [11.365, 11.365, 11.365]                  0.060   
17                           [14.973, 14.973, 14.973]                 63.041   
18                           [15.666, 15.666, 15.666]                 25.122   
19                           [14.922, 14.922, 14.922]                 14.928   

    vina_score_after_min                                        output_path  
0                 -5.613  ./vina_scoring/8A2D_11_ligand_014_minimized.pdbqt  
1                 -5.011  ./vina_scoring/8A2D_11_ligand_018_minimized.pdbqt  
2      

In [10]:
def vina_scoring_selector(show_pockets, show_drug_score, show_surface, show_vina_box, ligand_style, idx):
    # Receptor related variables
    scoring_row = vina_scores_filtered.iloc[idx]
    receptor_name = scoring_row['receptor_name']
    receptor_path = dirs_dict['prepared_receptors'] + receptor_name + '.pdbqt'
    pocket_paths = sorted(glob.glob(dirs_dict['prepared_receptors'] + receptor_name + '_out/*.pqr'))
    pockets_data = pd.read_csv(dirs_dict['prepared_receptors'] + 'fp_' + receptor_name + '.csv',sep=' ',index_col=[0])
    # Ligands related variables
    output_path = scoring_row['output_path']
    # pdbqt_mol = PDBQTMolecule.from_file(output_path, skip_typing=True)
    # rdkitmol_list = RDKitMolCreate.from_pdbqt_mol(pdbqt_mol)
    utils.pdbqt_to_sdf(pdbqt_file=output_path, output=dirs_dict['vina_scoring']+'aux_vina_out_sdf.sdf', include_data=False)
    rdkitmol_list = Chem.SDMolSupplier(dirs_dict['vina_scoring']+'aux_vina_out_sdf.sdf')
    
    # 3d plot
    visualize_molecules.show_3d_vina_score_dock(receptor_path, receptor_name, show_pockets, show_drug_score, show_surface, 
                                                show_vina_box, ligand_style, rdkitmol_list, pocket_paths, pockets_data, 
                                                scoring_row, False).show()
    
    # Display selected row from dataframe
    display(vina_scores_filtered.iloc[[idx]])

# Interactive widgets
ipywidgets.interact(vina_scoring_selector, 
                    idx = ipywidgets.IntSlider(min=0,max=len(vina_scores_filtered)-1, step=1),
                    show_pockets = ipywidgets.Checkbox(value=False, description='show pockets'),
                    show_drug_score = ipywidgets.Checkbox(value=False, description='show pockets drug_score'),
                    show_surface = ipywidgets.Checkbox(value=False, description='show surface'),
                    show_vina_box = ipywidgets.Checkbox(value=False, description='show box used for vina'),
                    ligand_style = ipywidgets.Dropdown(options=['line', 'stick', 'sphere'], value='stick', description='ligand style:'),
        )

interactive(children=(Checkbox(value=False, description='show pockets'), Checkbox(value=False, description='sh…

<function __main__.vina_scoring_selector(show_pockets, show_drug_score, show_surface, show_vina_box, ligand_style, idx)>

## visualize dockings

In [11]:
vina_dockings = pd.read_csv(dirs_dict['vina_docking']+'vina_dockings.csv',sep='\t')
vina_dockings

receptor_name pocket_id ligand_name  vina_docking_best  \
0           8A2D   8A2D_11  ligand_007             -8.259   
1           8A2D   8A2D_11  ligand_015             -7.289   
2           8A2A   8A2A_14  ligand_013             -6.315   
3           7U9A   7U9A_17  ligand_009             -5.947   
4           8A2D   8A2D_11  ligand_014             -5.737   
5           7JXQ   7JXQ_17  ligand_008             -5.729   
6           7JXQ   7JXQ_17  ligand_007             -5.683   
7           7U98   7U98_17  ligand_013             -5.549   
8           8A2D   8A2D_11  ligand_018             -5.541   
9           8A27   8A27_12  ligand_006             -5.472   
10          8A2D   8A2D_11  ligand_003             -5.327   
11          8A2D   8A2D_11  ligand_017             -5.310   
12          7U9A   7U9A_17  ligand_010             -5.284   
13          8A2A   8A2A_14  ligand_005             -5.154   
14          3IKA    3IKA_6  ligand_015             -5.147   
15          4LQM    4LQM_7  ligand_014             -5.140   
16          7U9A   7U9A_17  ligand_011             -4.869   
17          8A2A   8A2A_14  ligand_019             -4.680   
18          7JXQ   7JXQ_17  ligand_009             -4.584   
19          4LQM    4LQM_7  ligand_018             -4.159   

                         vina_docking_values  \
0    [-8.259, -8.253, -7.794, -7.787, -7.75]   
1    [-7.289, -7.03, -6.902, -6.842, -6.689]   
2    [-6.315, -6.274, -5.782, -5.777, -5.77]   
3        [-5.947, -5.7, -5.48, -5.1, -5.083]   
4    [-5.737, -5.71, -5.667, -5.556, -5.358]   
5   [-5.729, -5.634, -5.589, -5.482, -5.342]   
6    [-5.683, -5.414, -5.34, -5.297, -5.236]   
7       [-5.549, -5.4, -5.322, -5.228, -5.2]   
8   [-5.541, -5.249, -5.159, -5.146, -5.028]   
9   [-5.472, -5.052, -4.951, -4.801, -4.762]   
10  [-5.327, -4.952, -4.883, -4.856, -4.814]   
11   [-5.31, -5.308, -5.278, -5.187, -5.093]   
12  [-5.284, -5.184, -5.104, -4.996, -4.974]   
13  [-5.154, -4.856, -4.846, -4.784, -4.766]   
14   [-5.147, -5.03, -4.856, -4.855, -4.844]   
15   [-5.14, -5.108, -5.031, -4.867, -4.746]   
16   [-4.869, -4.866, -4.846, -4.81, -4.788]   
17   [-4.68, -4.661, -4.456, -4.414, -4.388]   
18  [-4.584, -4.291, -4.161, -4.139, -3.934]   
19   [-4.159, -3.957, -3.92, -3.872, -3.754]   

                                    pocket_box_center  \
0   [-8.102499961853027, -12.559500217437744, 16.4...   
1   [-8.102499961853027, -12.559500217437744, 16.4...   
2   [-8.648499727249146, -4.48550009727478, -20.59...   
3   [48.04050064086914, -4.1730000004172325, 31.27...   
4   [-8.102499961853027, -12.559500217437744, 16.4...   
5   [16.832000255584717, -40.72749900817871, -24.2...   
6   [16.832000255584717, -40.72749900817871, -24.2...   
7   [8.579499959945679, 20.399500846862793, 19.754...   
8   [-8.102499961853027, -12.559500217437744, 16.4...   
9   [-12.836000442504883, -14.669999599456787, -19...   
10  [-8.102499961853027, -12.559500217437744, 16.4...   
11  [-8.102499961853027, -12.559500217437744, 16.4...   
12  [48.04050064086914, -4.1730000004172325, 31.27...   
13  [-8.648499727249146, -4.48550009727478, -20.59...   
14  [-7.528500080108643, 13.613500118255615, 14.26...   
15  [-66.83650207519531, 4.127000093460083, -25.58...   
16  [48.04050064086914, -4.1730000004172325, 31.27...   
17  [-8.648499727249146, -4.48550009727478, -20.59...   
18  [16.832000255584717, -40.72749900817871, -24.2...   
19  [-66.83650207519531, 4.127000093460083, -25.58...   

                                        vina_box_size  \
0                            [15.652, 15.652, 15.652]   
1                            [15.666, 15.666, 15.666]   
2                            [14.973, 14.973, 14.973]   
3                            [11.365, 11.365, 11.365]   
4                            [10.782, 10.782, 10.782]   
5                               [15.56, 15.56, 15.56]   
6                            [15.652, 15.652, 15.652]   
7                            [14.973, 14.973, 14.973]   
8

In [12]:
def vina_docking_selector(show_pockets, show_drug_score, show_surface, show_vina_box, show_only_best_pose, ligand_style, idx):
    # Receptor related variables
    scoring_row = vina_dockings.iloc[idx]
    receptor_name = scoring_row['receptor_name']
    receptor_path = dirs_dict['prepared_receptors'] + receptor_name + '.pdbqt'
    pocket_paths = sorted(glob.glob(dirs_dict['prepared_receptors'] + receptor_name + '_out/*.pqr'))
    pockets_data = pd.read_csv(dirs_dict['prepared_receptors'] + 'fp_' + receptor_name + '.csv',sep=' ',index_col=[0])
    # Ligands related variables
    output_path = scoring_row['output_path']
    # pdbqt_mol = PDBQTMolecule.from_file(output_path, skip_typing=True)
    # rdkitmol_list = RDKitMolCreate.from_pdbqt_mol(pdbqt_mol)
    utils.pdbqt_to_sdf(pdbqt_file=output_path, output=dirs_dict['vina_docking']+'aux_vina_out_sdf.sdf')
    rdkitmol_list = Chem.SDMolSupplier(dirs_dict['vina_docking']+'aux_vina_out_sdf.sdf')
    
    # 3d plot
    visualize_molecules.show_3d_vina_score_dock(receptor_path, receptor_name, show_pockets, show_drug_score, show_surface, 
                                                show_vina_box, ligand_style, rdkitmol_list, pocket_paths, pockets_data, 
                                                scoring_row, show_only_best_pose).show()
    
    # Display selected row from dataframe
    display(vina_dockings.iloc[[idx]])

# Interactive widgets
ipywidgets.interact(vina_docking_selector, 
                    idx = ipywidgets.IntSlider(min=0,max=len(vina_dockings)-1, step=1),
                    show_pockets = ipywidgets.Checkbox(value=False, description='show pockets'),
                    show_drug_score = ipywidgets.Checkbox(value=False, description='show pockets drug_score'),
                    show_surface = ipywidgets.Checkbox(value=False, description='show surface'),
                    show_vina_box = ipywidgets.Checkbox(value=False, description='show box used for vina'),
                    show_only_best_pose = ipywidgets.Checkbox(value=False, description='show only the best pose'),
                    ligand_style = ipywidgets.Dropdown(options=['line', 'stick', 'sphere'], value='stick', description='ligand style:'),
        )

interactive(children=(Checkbox(value=False, description='show pockets'), Checkbox(value=False, description='sh…

<function __main__.vina_docking_selector(show_pockets, show_drug_score, show_surface, show_vina_box, show_only_best_pose, ligand_style, idx)>

## example interactive view

In [28]:
from IPython.display import HTML 
from base64 import b64encode

path = "/home/jovyan/vina_docking/media/vina_docking_3d_view.mp4"
mp4 = open(path,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()

def display_video(path):  
    mp4 = open(path,'rb').read()   
    data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
    display(
      HTML(
      """
          <video width=400 controls>
                <source src="%s" type="video/mp4">
          </video>
      """ % data_url
           )   
    )
display_video(path)